# Capstone Project - The Battle of the Neighborhoods (Week 2)
### Applied Data Science Capstone by IBM/Coursera

## Table of contents
* [Introduction: Business Problem](#introduction)
* [Data](#data)
* [Methodology](#methodology)
* [Analysis](#analysis)
* [Results and Discussion](#results)
* [Conclusion](#conclusion)

## Introduction: Business Problem <a name="introduction"></a>

In this project we will try to find an optimal location for a restaurant. Specifically, this report will be targeted to stakeholders interested in opening a **vegan restaurant** in **Sao Paulo**, Brazil.

Since there are lots of restaurants in Sao Paulo we will try to detect **locations that are not already crowded with restaurants**. We are also particularly interested in **areas with no vegan restaurants in vicinity**. We would also prefer locations **as near as possible to the Bixiga neighborhood**, which is famous for great restaurants, where many people go there just to eat.

We will use our data science powers to generate a few most promissing neighborhoods based on this criteria. Advantages of each area will then be clearly expressed so that best possible final location can be chosen by stakeholders.

## Data <a name="data"></a>

Based on definition of our problem, factors that will influence our decission are:
* number of existing restaurants in the neighborhood (any type of restaurant)
* number of and distance to vegan restaurants in the neighborhood, if any
* distance of neighborhood from Bixiga area

We decided to use regularly spaced grid of locations, centered around city center, to define our neighborhoods.

Following data sources will be needed to extract/generate the required information:
* centers of candidate areas will be generated algorithmically and approximate addresses of centers of those areas will be obtained using **Google Maps API reverse geocoding**
* number of restaurants and their type and location in every neighborhood will be obtained using **Foursquare API**
* coordinate of the Bixiga neighborhood in Sao Paulo  will be obtained using **Google Maps API geocoding**

### Neighborhood Candidates

Let's create latitude & longitude coordinates for centroids of our candidate neighborhoods. We will create a grid of cells covering our area of interest which is aprox. 12x12 killometers centered around the Bixiga neighborhood.

Let's first find the latitude & longitude of the Bixiga neighborhood, using specific, well known address and Google Maps geocoding API.

In [14]:
pip install geocoder

Note: you may need to restart the kernel to use updated packages.


In [15]:
import requests

def get_coordinates(api_key, address, verbose=False):
    try:
        url = 'https://maps.googleapis.com/maps/api/geocode/json?key={}&address={}'.format(api_key, address)
        response = requests.get(url).json()
        if verbose:
            print('Google Maps API JSON result =>', response)
        results = response['results']
        geographical_data = results[0]['geometry']['location'] # get geographical coordinates
        lat = geographical_data['lat']
        lon = geographical_data['lng']
        return [lat, lon]
    except:
        return [None, None]
    
address = 'Bixiga, Sao Paulo, Brazil'
bixiga = get_coordinates(google_api_key, address)
print('Coordinate of {}: {}'.format(address, bixiga))

Coordinate of Bixiga, Sao Paulo, Brazil: [-23.5574698, -46.6457942]


Now let's create a grid of area candidates, equaly spaced, centered around Bixiga and within ~6km from it. Our neighborhoods will be defined as circular areas with a radius of 300 meters, so our neighborhood centers will be 600 meters apart.

To accurately calculate distances we need to create our grid of locations in Cartesian 2D coordinate system which allows us to calculate distances in meters (not in latitude/longitude degrees). Then we'll project those coordinates back to latitude/longitude degrees to be shown on Folium map. So let's create functions to convert between WGS84 spherical coordinate system (latitude/longitude degrees) and UTM Cartesian coordinate system (X/Y coordinates in  meters).

In [16]:
pip install Shapely-1.6.4.post1-cp37-cp37m-win_amd64.whl

Note: you may need to restart the kernel to use updated packages.


In [17]:
pip install pyproj

Note: you may need to restart the kernel to use updated packages.


In [18]:
#!pip install shapely
import shapely.geometry

#!pip install pyproj
import pyproj

import math

def lonlat_to_xy(lon, lat):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
    return xy[0], xy[1]

def xy_to_lonlat(x, y):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
    return lonlat[0], lonlat[1]

def calc_xy_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)

print('Coordinate transformation check')
print('-------------------------------')
print('Bixiga longitude={}, latitude={}'.format(bixiga[1], bixiga[0]))
x, y = lonlat_to_xy(bixiga[1], bixiga[0])
print('Bixiga UTM X={}, Y={}'.format(x, y))
lo, la = xy_to_lonlat(x, y)
print('Bixiga longitude={}, latitude={}'.format(lo, la))

Coordinate transformation check
-------------------------------
Bixiga longitude=-46.6457942, latitude=-23.5574698
Bixiga UTM X=-6630364.306365894, Y=-4731198.949076099
Bixiga longitude=-46.645794200003884, latitude=-23.557469800002476


Let's create a **hexagonal grid of cells**: we offset every other row, and adjust vertical row spacing so that **every cell center is equally distant from all it's neighbors**.

In [19]:
bixiga_x, bixiga_y = lonlat_to_xy(bixiga[1], bixiga[0]) # Bexiga in Cartesian coordinates

k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_min = bixiga_x - 6000
x_step = 600
y_min = bixiga_y - 6000 - (int(21/k)*k*600 - 12000)/2
y_step = 600 * k 

latitudes = []
longitudes = []
distances_from_center = []
xs = []
ys = []
for i in range(0, int(21/k)):
    y = y_min + i * y_step
    x_offset = 300 if i%2==0 else 0
    for j in range(0, 21):
        x = x_min + j * x_step + x_offset
        distance_from_center = calc_xy_distance(bixiga_x, bixiga_y, x, y)
        if (distance_from_center <= 6001):
            lon, lat = xy_to_lonlat(x, y)
            latitudes.append(lat)
            longitudes.append(lon)
            distances_from_center.append(distance_from_center)
            xs.append(x)
            ys.append(y)

print(len(latitudes), 'candidate neighborhood centers generated.')

364 candidate neighborhood centers generated.


Let's visualize the data we have so far: city center location and candidate neighborhood centers:

In [20]:
import folium

In [58]:
map_bixiga = folium.Map(location=bixiga, zoom_start=13)
folium.Marker(bixiga, popup='Bixiga').add_to(map_bixiga)
for lat, lon in zip(latitudes, longitudes):
    #folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_bixiga) 
    folium.Circle([lat, lon], radius=300, color='blue', fill=False).add_to(map_bixiga)
    #folium.Marker([lat, lon]).add_to(map_bixiga)
map_bixiga

OK, we now have the coordinates of centers of neighborhoods/areas to be evaluated, equally spaced (distance from every point to it's neighbors is exactly the same) and within ~6km from Bixiga.

Let's now use Google Maps API to get approximate addresses of those locations.

In [22]:
def get_address(api_key, latitude, longitude, verbose=False):
    try:
        url = 'https://maps.googleapis.com/maps/api/geocode/json?key={}&latlng={},{}'.format(api_key, latitude, longitude)
        response = requests.get(url).json()
        if verbose:
            print('Google Maps API JSON result =>', response)
        results = response['results']
        address = results[0]['formatted_address']
        return address
    except:
        return None

addr = get_address(google_api_key, bixiga[0], bixiga[1])
print('Reverse geocoding check')
print('-----------------------')
print('Address of [{}, {}] is: {}'.format(bixiga[0], bixiga[1], addr))

Reverse geocoding check
-----------------------
Address of [-23.5574698, -46.6457942] is: R. Rui Barbosa, 218 - Bela Vista, São Paulo - SP, 01326-010, Brazil


In [23]:
print('Obtaining location addresses: ', end='')
addresses = []
for lat, lon in zip(latitudes, longitudes):
    address = get_address(google_api_key, lat, lon)
    if address is None:
        address = 'NO ADDRESS'
    address = address.replace(', Brazil', '') # We don't need country part of address
    addresses.append(address)
    print(' .', end='')
print(' done.')

Obtaining location addresses:  . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


In [24]:
addresses[150:170]

['Praça Prof. Belmiro Nascimento Martins, 1575 - Jardim Nossa Sra. Aparecida, São Paulo - SP, 04108-120',
 'R. Cel. Diogo, 213 - Jardim da Gloria, São Paulo - SP, 01544-020',
 'R. Laurindo Rabêlo, 20 - Jardim da Gloria, São Paulo - SP, 01546-020',
 'R. Alto das Perdizes, 69 - Perdizes, São Paulo - SP, 05014-060',
 'R. Heitor de Morais, 629 - Pacaembu, São Paulo - SP',
 'R. Ubatuba, 98 - Pacaembu, São Paulo - SP, 01248-030',
 'Rua Itápolis, 591 - Pacaembu, São Paulo - SP, 01243-080',
 'R. Goiás, 147 - Higienópolis, São Paulo - SP, 01244-030',
 'R. Cel. José Eusébio, 11 - Higienópolis, São Paulo - SP, 01239-030',
 'R. Augusta, 1088 - Consolação, São Paulo - SP, 01304-001',
 'R. Herculano de Freitas, 191 - Bela Vista, São Paulo - SP, 01308-020',
 'R. Itapeva, 66 - Bela Vista, São Paulo - SP, 01332-000',
 'R. dos Franceses, 177 - Morro dos Ingleses, São Paulo - SP, 01329-010',
 'R. Pedroso, 628 - Bela Vista, São Paulo - SP, 01322-010',
 'R. Santa Madalena, 81 - Liberdade, São Paulo - SP, 0

Looking good. Let's now place all this into a Pandas dataframe.

In [25]:
import pandas as pd

df_locations = pd.DataFrame({'Address': addresses,
                             'Latitude': latitudes,
                             'Longitude': longitudes,
                             'X': xs,
                             'Y': ys,
                             'Distance from bixiga': distances_from_center})

df_locations.head(10)

Address   Latitude  Longitude  \
0  R. França, 189 - Jardim Europa, São Paulo - SP... -23.576098 -46.673939   
1  Av. São Gabriel, 605 - Itaim Bibi, São Paulo -... -23.578017 -46.671163   
2  Rua Claudina Silva, 75 - Jardim Paulista, São ... -23.579935 -46.668387   
3  Av. Brigadeiro Luís Antônio, 4595 - Jardim Pau... -23.581854 -46.665611   
4  Av. República do Líbano, 331 - Ibirapuera, São... -23.583772 -46.662835   
5  Unnamed Road - Ibirapuera, São Paulo - SP, 040... -23.585691 -46.660058   
6  Ibirapuera Park - Av. Pedro Álvares Cabral - V... -23.587610 -46.657281   
7  Rua Groenlândia, 1555 - Jardim America, São Pa... -23.571006 -46.676299   
8  R. México, 715 - Jardim Paulista, São Paulo - ... -23.572924 -46.673524   
9  R. Chile, 17 - Jardim America, São Paulo - SP,... -23.574842 -46.670749   

              X             Y  Distance from bixiga  
0 -6.632164e+06 -4.736915e+06           5992.495307  
1 -6.631564e+06 -4.736915e+06           5840.376700  
2 -6.630964e+06 -4.736915e+06           5747.173218  
3 -6.630364e+06 -4.736915e+06           5715.767665  
4 -6.629764e+06 -4.736915e+06           5747.173218  
5 -6.629164e+06 -4.736915e+06           5840.376700  
6 -6.628564e+06 -4.736915e+06           5992.495307  
7 -6.633064e+06 -4.736395e+06           5855.766389  
8 -6.632464e+06 -4.736395e+06           5604.462508  
9 -6.631864e+06 -4.736395e+06           5408.326913

...and let's now save/persist this data into local file.

In [26]:
df_locations.to_pickle('./locations.pkl')

### Foursquare
Now that we have our location candidates, let's use Foursquare API to get info on restaurants in each neighborhood.

We're interested in venues in 'food' category, but only those that are proper restaurants - coffe shops, pizza places, bakeries etc. are not direct competitors so we don't care about those. So we will include in out list only venues that have 'restaurant' in category name, and we'll make sure to detect and include all the subcategories of specific 'Vegan restaurant' category, as we need info on vegan restaurants in the neighborhood.

Foursquare credentials are defined in hidden cell bellow.

In [27]:
client_id = 'KBRDIKWNWSKUIWKLOLQLMT2XUMYYWSCE5BOBNJA0LILN4OSP' # your Foursquare ID
client_secret = 'JOYF0EHX23P0DUIO3SE4HQPYXCUVDIUYPJ0JKWBODXBSZGYO' # your Foursquare Secret
version = '20180605' # Foursquare API version

In [28]:
# Category IDs corresponding to vegan restaurants were taken from Foursquare web site (https://developer.foursquare.com/docs/resources/categories):

food_category = '4d4b7105d754a06374d81259' # 'Root' category for all food-related venues

vegan_restaurant_categories = ['4bf58dd8d48988d1d3941735']

def is_restaurant(categories, specific_filter=None):
    restaurant_words = ['restaurant', 'vegan']
    restaurant = False
    specific = False
    for c in categories:
        category_name = c[0].lower()
        category_id = c[1]
        for r in restaurant_words:
            if r in category_name:
                restaurant = True
        if 'fast food' in category_name:
            restaurant = False
        if not(specific_filter is None) and (category_id in specific_filter):
            specific = True
            restaurant = True
    return restaurant, specific

def get_categories(categories):
    return [(cat['name'], cat['id']) for cat in categories]

def format_address(location):
    address = ', '.join(location['formattedAddress'])
    address = address.replace(', Brasil', '')
    return address

def get_venues_near_location(lat, lon, category, client_id, client_secret, radius=500, limit=100):
    url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&categoryId={}&radius={}&limit={}'.format(
        client_id, client_secret, version, lat, lon, category, radius, limit)
    try:
        results = requests.get(url).json()['response']['groups'][0]['items']
        venues = [(item['venue']['id'],
                   item['venue']['name'],
                   get_categories(item['venue']['categories']),
                   (item['venue']['location']['lat'], item['venue']['location']['lng']),
                   format_address(item['venue']['location']),
                   item['venue']['location']['distance']) for item in results]        
    except:
        venues = []
    return venues

In [29]:
# Let's now go over our neighborhood locations and get nearby restaurants; we'll also maintain a dictionary of all found restaurants and all found vegan restaurants

import pickle

def get_restaurants(lats, lons):
    restaurants = {}
    vegan_restaurants = {}
    location_restaurants = []

    print('Obtaining venues around candidate locations:', end='')
    for lat, lon in zip(lats, lons):
        # Using radius=350 to meke sure we have overlaps/full coverage so we don't miss any restaurant (we're using dictionaries to remove any duplicates resulting from area overlaps)
        venues = get_venues_near_location(lat, lon, food_category, client_id, client_secret, radius=350, limit=100)
        area_restaurants = []
        for venue in venues:
            venue_id = venue[0]
            venue_name = venue[1]
            venue_categories = venue[2]
            venue_latlon = venue[3]
            venue_address = venue[4]
            venue_distance = venue[5]
            is_res, is_vegan = is_restaurant(venue_categories, specific_filter=vegan_restaurant_categories)
            if is_res:
                x, y = lonlat_to_xy(venue_latlon[1], venue_latlon[0])
                restaurant = (venue_id, venue_name, venue_latlon[0], venue_latlon[1], venue_address, venue_distance, is_vegan, x, y)
                if venue_distance<=300:
                    area_restaurants.append(restaurant)
                restaurants[venue_id] = restaurant
                if is_vegan:
                    vegan_restaurants[venue_id] = restaurant
        location_restaurants.append(area_restaurants)
        print(' .', end='')
    print(' done.')
    return restaurants, vegan_restaurants, location_restaurants

# Try to load from local file system in case we did this before
restaurants = {}
vegan_restaurants = {}
location_restaurants = []
loaded = False
try:
    with open('restaurants_350.pkl', 'rb') as f:
        restaurants = pickle.load(f)
    with open('vegan_restaurants_350.pkl', 'rb') as f:
        vegan_restaurants = pickle.load(f)
    with open('location_restaurants_350.pkl', 'rb') as f:
        location_restaurants = pickle.load(f)
    print('Restaurant data loaded.')
    loaded = True
except:
    pass

# If load failed use the Foursquare API to get the data
if not loaded:
    restaurants, vegan_restaurants, location_restaurants = get_restaurants(latitudes, longitudes)
    
    # Let's persists this in local file system
    with open('restaurants_350.pkl', 'wb') as f:
        pickle.dump(restaurants, f)
    with open('vegan_restaurants_350.pkl', 'wb') as f:
        pickle.dump(vegan_restaurants, f)
    with open('location_restaurants_350.pkl', 'wb') as f:
        pickle.dump(location_restaurants, f)

Restaurant data loaded.


In [30]:
import numpy as np

print('Total number of restaurants:', len(restaurants))
print('Total number of vegan restaurants:', len(vegan_restaurants))
print('Percentage of vegan restaurants: {:.2f}%'.format(len(vegan_restaurants) / len(restaurants) * 100))
print('Average number of restaurants in neighborhood:', np.array([len(r) for r in location_restaurants]).mean())

Total number of restaurants: 1818
Total number of vegan restaurants: 53
Percentage of vegan restaurants: 2.92%
Average number of restaurants in neighborhood: 10.365384615384615


In [31]:
print('List of all restaurants')
print('-----------------------')
for r in list(restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(restaurants))

List of all restaurants
-----------------------
('4f6bc26ce4b05c9c2947296f', 'Zaatar - Lanchonete Árabe', -23.57816292347061, -46.674644465126576, 'Av. 9 de julho, 5143, São Paulo, SP, 01407-200, Brasil', 240, False, -6632029.518341578, -4737297.925214622)
('55c54e9e498e1c44d408101c', 'Dalmo Bárbaro', -23.579623905945613, -46.67032745748452, 'R. Gironda, 188, São Paulo, SP, 01435-040, Brasil', 200, False, -6631267.751363751, -4737069.304136488)
('4c03ea410d0e0f47f32f039a', 'Kilo & Co Restaurante', -23.57940827334059, -46.673422469258746, 'Rua itacema 274 (Esquina com rua Japão), São Paulo, SP, Brasil', 277, False, -6631720.238234493, -4737358.066459574)
('4b7c11f7f964a5202f7b2fe3', 'Gira Sol', -23.57839667285503, -46.67105731497329, 'Av. São Gabriel, 545 (R. Itacema), São Paulo, SP, Brasil', 321, False, -6631506.877799788, -4736960.805894614)
('4f3bc531e4b03e9c37468b88', 'Hamburguinho', -23.578108035548016, -46.67454455605467, 'R. Dr. Renato Paes de Barros, 85 - Itaim Bibi, São Paulo, 

In [32]:
print('List of vegan restaurants')
print('---------------------------')
for r in list(vegan_restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(vegan_restaurants))

List of vegan restaurants
---------------------------
('52b0764b11d20c46680e3d83', 'Super Natural', -23.566365074531973, -46.668847215047194, 'Rua Augusta, 2992, São Paulo, SP, Brasil', 236, True, -6632555.228726885, -4734925.090406561)
('4b992203f964a5209e6335e3', 'Natural da Vila', -23.58908693378926, -46.63913142297381, 'R. Major Maragliano, 375, São Paulo, SP, 04017-030, Brasil', 297, True, -6625887.99724414, -4735255.146639328)
('579b7be938fadf93f3014e67', 'Cultura Veg', -23.58885, -46.639164, 'Rua Major Maragliano, 387, São Paulo, SP, 04017-030, Brasil', 271, True, -6625919.138781855, -4735222.967864649)
('4bfea15c05672d7f346c0a04', 'Casa Jaya', -23.558991814705305, -46.67505482541989, 'R. Capote Valente, 305 (R. Artur De Azevedo), São Paulo, SP, 05409-000, Brasil', 86, True, -6634244.489866029, -4734461.811820543)
('5878ffe96cea3f55dc0604c8', 'Vegano SP', -23.55796312628988, -46.679512124964894, 'Rua João Moura, 901, São Paulo, SP, 05412-002, Brasil', 276, True, -6634977.4637310

In [33]:
print('Restaurants around location')
print('---------------------------')
for i in range(100, 110):
    rs = location_restaurants[i][:8]
    names = ', '.join([r[1] for r in rs])
    print('Restaurants around location {}: {}'.format(i+1, names))

Restaurants around location
---------------------------
Restaurants around location 101: Ema Restaurante, All Day Restaurante, Jambú Gastronomia, L'Osteria do Piero, Mama Bistrô, Tappo Trattoria, Apfel Restaurante Vegetariano, Tuela Grill
Restaurants around location 102: Hi Pokee, Ema Restaurante, Amadeus, Terraço Jardins, Cantina do Piero il Vero, Guna Vegan, Loving Hut, Apfel Restaurante Vegetariano
Restaurants around location 103: Capim Santo, Calle 54, Hakka Sushi, Guna Vegan, Loving Hut, Ser-Afim, Restaurante Panorâmico, New Paulista Restaurante
Restaurants around location 104: Seen, Calle 54, Old House Restaurante, Sham Cozinha Árabe, Club Life To Go, Ikioi Capricho Oriental, Ser-Afim, Bistrô Tivoli
Restaurants around location 105: Osteria Generale, Manai Gastronomia, Sí Señor!, Seen, Cantina Nipolitana, Almanara, Sham Cozinha Árabe, Rinconcito Peruano
Restaurants around location 106: Ráscal, Bueno Cozinha Oriental, Keito, Kan Suke, Sushi Guen | 寿司源, America, Yakitori Mizusaka - 

Let's now see all the collected restaurants in our area of interest on map, and let's also show vegan restaurants in different color.

In [59]:
map_bixiga = folium.Map(location=bixiga, zoom_start=13)
folium.Marker(bixiga, popup='Bixiga').add_to(map_bixiga)
for res in restaurants.values():
    lat = res[2]; lon = res[3]
    is_vegan = res[6]
    color = 'red' if is_vegan else 'blue'
    folium.CircleMarker([lat, lon], radius=3, color=color, fill=True, fill_color=color, fill_opacity=1).add_to(map_bixiga)
map_bixiga

Looking good. So now we have all the restaurants in area within few kilometers from Bixiga, and we know which ones are vegan restaurants! We also know which restaurants exactly are in vicinity of every neighborhood candidate center.

This concludes the data gathering phase - we're now ready to use this data for analysis to produce the report on optimal locations for a new vegan restaurant!

## Methodology <a name="methodology"></a>

In this project we will direct our efforts on detecting areas of Sao Paulo that have an average density of restaurants that is not so big, particularly those with low number of vegan restaurants. We will limit our analysis to area ~6km around the Bixiga neighborhood.

In first step we have collected the required **data: location and type (category) of every restaurant within 6km from Bixiga**. We have also **identified vegan restaurants** (according to Foursquare categorization).

Second step in our analysis will be calculation and exploration of '**restaurant density**' across different areas of Sao Paulo - we will use **heatmaps** to identify a few promising areas close to Bixiga with low number of restaurants in general (*and* no vegan restaurants in vicinity) and focus our attention on those areas.

In third and final step we will focus on most promising areas and within those create **clusters of locations that meet some basic requirements** established in discussion with stakeholders: we will take into consideration locations with **no more than two restaurants in radius of 250 meters**, and we want locations **without vegan restaurants in radius of 400 meters**. We will present map of all such locations but also create clusters (using **k-means clustering**) of those locations to identify general zones / neighborhoods / addresses which should be a starting point for final 'street level' exploration and search for optimal venue location by stakeholders.

## Analysis <a name="analysis"></a>

Let's perform some basic explanatory data analysis and derive some additional info from our raw data. First let's count the **number of restaurants in every area candidate**:

In [35]:
location_restaurants_count = [len(res) for res in location_restaurants]

df_locations['Restaurants in area'] = location_restaurants_count

print('Average number of restaurants in every area with radius=300m:', np.array(location_restaurants_count).mean())

df_locations.head(10)

Average number of restaurants in every area with radius=300m: 10.365384615384615


Address   Latitude  Longitude  \
0  R. França, 189 - Jardim Europa, São Paulo - SP... -23.576098 -46.673939   
1  Av. São Gabriel, 605 - Itaim Bibi, São Paulo -... -23.578017 -46.671163   
2  Rua Claudina Silva, 75 - Jardim Paulista, São ... -23.579935 -46.668387   
3  Av. Brigadeiro Luís Antônio, 4595 - Jardim Pau... -23.581854 -46.665611   
4  Av. República do Líbano, 331 - Ibirapuera, São... -23.583772 -46.662835   
5  Unnamed Road - Ibirapuera, São Paulo - SP, 040... -23.585691 -46.660058   
6  Ibirapuera Park - Av. Pedro Álvares Cabral - V... -23.587610 -46.657281   
7  Rua Groenlândia, 1555 - Jardim America, São Pa... -23.571006 -46.676299   
8  R. México, 715 - Jardim Paulista, São Paulo - ... -23.572924 -46.673524   
9  R. Chile, 17 - Jardim America, São Paulo - SP,... -23.574842 -46.670749   

              X             Y  Distance from bixiga  Restaurants in area  
0 -6.632164e+06 -4.736915e+06           5992.495307                    1  
1 -6.631564e+06 -4.736915e+06           5840.376700                    3  
2 -6.630964e+06 -4.736915e+06           5747.173218                    2  
3 -6.630364e+06 -4.736915e+06           5715.767665                    1  
4 -6.629764e+06 -4.736915e+06           5747.173218                    2  
5 -6.629164e+06 -4.736915e+06           5840.376700                    2  
6 -6.628564e+06 -4.736915e+06           5992.495307                    3  
7 -6.633064e+06 -4.736395e+06           5855.766389                    1  
8 -6.632464e+06 -4.736395e+06           5604.462508                    1  
9 -6.631864e+06 -4.736395e+06           5408.326913                    0

OK, now let's calculate the **distance to nearest vegan restaurant from every area candidate center** (not only those within 300m - we want distance to closest one, regardless of how distant it is).

In [36]:
distances_to_vegan_restaurant = []

for area_x, area_y in zip(xs, ys):
    min_distance = 10000
    for res in vegan_restaurants.values():
        res_x = res[7]
        res_y = res[8]
        d = calc_xy_distance(area_x, area_y, res_x, res_y)
        if d<min_distance:
            min_distance = d
    distances_to_vegan_restaurant.append(min_distance)

df_locations['Distance to vegan restaurant'] = distances_to_vegan_restaurant

In [37]:
df_locations.head(10)

Address   Latitude  Longitude  \
0  R. França, 189 - Jardim Europa, São Paulo - SP... -23.576098 -46.673939   
1  Av. São Gabriel, 605 - Itaim Bibi, São Paulo -... -23.578017 -46.671163   
2  Rua Claudina Silva, 75 - Jardim Paulista, São ... -23.579935 -46.668387   
3  Av. Brigadeiro Luís Antônio, 4595 - Jardim Pau... -23.581854 -46.665611   
4  Av. República do Líbano, 331 - Ibirapuera, São... -23.583772 -46.662835   
5  Unnamed Road - Ibirapuera, São Paulo - SP, 040... -23.585691 -46.660058   
6  Ibirapuera Park - Av. Pedro Álvares Cabral - V... -23.587610 -46.657281   
7  Rua Groenlândia, 1555 - Jardim America, São Pa... -23.571006 -46.676299   
8  R. México, 715 - Jardim Paulista, São Paulo - ... -23.572924 -46.673524   
9  R. Chile, 17 - Jardim America, São Paulo - SP,... -23.574842 -46.670749   

              X             Y  Distance from bixiga  Restaurants in area  \
0 -6.632164e+06 -4.736915e+06           5992.495307                    1   
1 -6.631564e+06 -4.736915e+06           5840.376700                    3   
2 -6.630964e+06 -4.736915e+06           5747.173218                    2   
3 -6.630364e+06 -4.736915e+06           5715.767665                    1   
4 -6.629764e+06 -4.736915e+06           5747.173218                    2   
5 -6.629164e+06 -4.736915e+06           5840.376700                    2   
6 -6.628564e+06 -4.736915e+06           5992.495307                    3   
7 -6.633064e+06 -4.736395e+06           5855.766389                    1   
8 -6.632464e+06 -4.736395e+06           5604.462508                    1   
9 -6.631864e+06 -4.736395e+06           5408.326913                    0   

   Distance to vegan restaurant  
0                   2027.666946  
1                   2222.732570  
2                   2394.634699  
3                   2369.120908  
4                   2492.226396  
5                   2744.020945  
6                   3093.236085  
7                   1555.664698  
8                   1472.820249  
9                   1624.286403

So, on average, **vegan restaurants can be found within ~2000m** from every area center candidate.

Let's create a map showing **heatmap / density of restaurants** and try to extract some meaningfull info from that. Also, let's show few circles indicating distance of 1km, 2km and 3km from Bixiga.

In [38]:
print('Average distance to closest vegan restaurant from each area center:', df_locations['Distance to vegan restaurant'].mean())

Average distance to closest vegan restaurant from each area center: 1002.5828532105602


In [39]:
pip install pygeoj

Note: you may need to restart the kernel to use updated packages.


In [40]:
import json

with open('map.json') as f:
    sp_boroughs = json.load(f)
     
for feature in sp_boroughs['features']:
    print(feature['geometry']['type'])
    print(feature['geometry']['coordinates'])
    
def boroughs_style(feature):
    return { 'color': 'blue', 'fill': False }

Polygon
[[[352436.869, 7394174.148], [352450.74, 7394171.541], [352468.533, 7394165.397], [352468.79, 7394165.296], [352469.049, 7394165.2], [352469.31, 7394165.108], [352469.572, 7394165.02], [352469.836, 7394164.938], [352470.101, 7394164.859], [352470.367, 7394164.786], [352470.635, 7394164.717], [352470.903, 7394164.653], [352471.173, 7394164.594], [352471.444, 7394164.539], [352471.716, 7394164.489], [352471.989, 7394164.444], [352472.262, 7394164.403], [352472.536, 7394164.367], [352472.81, 7394164.336], [352473.086, 7394164.31], [352473.361, 7394164.289], [352473.637, 7394164.272], [352473.913, 7394164.261], [352474.189, 7394164.254], [352474.466, 7394164.252], [352474.742, 7394164.255], [352475.018, 7394164.262], [352475.294, 7394164.275], [352475.57, 7394164.292], [352475.845, 7394164.314], [352476.12, 7394164.341], [352476.395, 7394164.372], [352476.669, 7394164.409], [352476.942, 7394164.45], [352477.215, 7394164.496], [352477.486, 7394164.547], [352477.757, 7394164.602], [3

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [41]:
restaurant_latlons = [[res[2], res[3]] for res in restaurants.values()]

vegan_latlons = [[res[2], res[3]] for res in vegan_restaurants.values()]

In [71]:
from folium import plugins
from folium.plugins import HeatMap

map_bixiga = folium.Map(location=bixiga, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_bixiga) #cartodbpositron cartodbdark_matter
HeatMap(restaurant_latlons).add_to(map_bixiga)
folium.Marker(bixiga).add_to(map_bixiga)
folium.Circle(bixiga, radius=1000, fill=False, color='white').add_to(map_bixiga)
folium.Circle(bixiga, radius=2000, fill=False, color='white').add_to(map_bixiga)
folium.Circle(bixiga, radius=3000, fill=False, color='white').add_to(map_bixiga)
#folium.GeoJson(sp_boroughs, style_function=boroughs_style, name='geojson').add_to(map_bixiga)
map_bixiga

Let's create another heatmap map showing **heatmap/density of vegan restaurants** only.

In [43]:
map_bixiga = folium.Map(location=bixiga, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_bixiga) #cartodbpositron cartodbdark_matter
HeatMap(vegan_latlons).add_to(map_bixiga)
folium.Marker(bixiga).add_to(map_bixiga)
folium.Circle(bixiga, radius=1000, fill=False, color='white').add_to(map_bixiga)
folium.Circle(bixiga, radius=2000, fill=False, color='white').add_to(map_bixiga)
folium.Circle(bixiga, radius=3000, fill=False, color='white').add_to(map_bixiga)
#folium.GeoJson(sp_boroughs, style_function=boroughs_style, name='geojson').add_to(map_bixiga)
map_bixiga

This map is not so 'hot', but it indicates higher density of existing vegan restaurants directly northeast and southwest from Bixiga center, with closest pockets of **low vegan restaurant density positioned on the remaining areas**.

Based on this we will now focus our analysis on areas *south-west, south, south-east and east from Berlin center* - we will move the center of our area of interest and reduce it's size to have a radius of **2.5km**. This places our location candidates mostly around the **Paulista Avenue**, where a lot people walk around, including tourists.

### The Paulista Avenue

Analysis of popular travel guides and web sites often mention the Paulista Avenue as interesting, rich with culture, and different people selling their art. Below is an overview of it given by Wikipedia (https://en.wikipedia.org/wiki/Paulista_Avenue):

*"Paulista Avenue (Avenida Paulista in Portuguese, Paulista being the demonym for those born in São Paulo state) is one of the most important avenues in São Paulo, Brazil. It stretches 2.8 kilometres (1.7 mi) and runs northwest to southeast. Its northwest point is Praça Marechal Cordeiro de Farias at its intersection with Rua da Consolação and its southeast point is Praça Oswaldo Cruz at its intersection with Treze de Maio, Bernardino de Campos, Desembargador Eliseu Guilherme, and Dr. Rafael de Barros avenues. Major crossroads on the street are Rua Augusta, Rua Haddock Lobo and Avenida Brigadeiro Luis Antonio. Parallel to it are Cincinato Braga, Joaquim Eugenio de Lima on the Bela Vista/Paraíso side and Alameda Santos and Coronel Oscar Freire on the Jardins side. Paulista Avenue crosses sections of the neighborhoods of Paraíso, Bela Vista, Jardim Paulista, Cerqueira César and Jardim América, ending in Higienópolis.*

*The headquarters of a large number of financial and cultural institutions are located on Paulista Avenue. As a symbol of the center of economic and political power of São Paulo it has been the focal point of numerous political protests beginning in 1929 and continuing into the 21st century. It is also home to an extensive shopping area and to South America's most comprehensive fine-art museum, MASP. Being one of the highest points in São Paulo, it is clustered with radio and TV stations antennae, most notably that of Rede Gazeta. Paulista Avenue is a major hub of the subway and bus lines of the city."*


Popular with tourists, alternative and bohemian but booming and trendy, relatively close to city center and well connected, ths region appears to justify further analysis.

Let's define new, more narrow region of interest, which will include low-restaurant-count parts arounf Paulista Avenue closest to Bixiga.

In [135]:
roi_x_min = bixiga_x - 2000
roi_y_max = bixiga_y + 1000
roi_width = 5000
roi_height = 5000
roi_center_x = roi_x_min + 2500
roi_center_y = roi_y_max - 2500
roi_center_lon, roi_center_lat = xy_to_lonlat(roi_center_x, roi_center_y)
roi_center = [roi_center_lat, roi_center_lon]

map_bixiga = folium.Map(location=roi_center, zoom_start=14)
HeatMap(restaurant_latlons).add_to(map_bixiga)
folium.Marker(bixiga).add_to(map_bixiga)
folium.Circle(roi_center, radius=3000, color='white', fill=True, fill_opacity=0.4).add_to(map_bixiga)
#folium.GeoJson(berlin_boroughs, style_function=boroughs_style, name='geojson').add_to(map_bixiga)
map_bixiga

Not bad - this nicely covers all the pockets of low restaurant density around the Paulista Avenue closest to the Bixiga neighborhood.

Let's also create new, more dense grid of location candidates restricted to our new region of interest (let's make our location candidates 100m appart).

In [126]:
k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_step = 100
y_step = 100 * k 
roi_y_min = roi_center_y - 2500

roi_latitudes = []
roi_longitudes = []
roi_xs = []
roi_ys = []
for i in range(0, int(51/k)):
    y = roi_y_min + i * y_step
    x_offset = 50 if i%2==0 else 0
    for j in range(0, 51):
        x = roi_x_min + j * x_step + x_offset
        d = calc_xy_distance(roi_center_x, roi_center_y, x, y)
        if (d <= 2501):
            lon, lat = xy_to_lonlat(x, y)
            roi_latitudes.append(lat)
            roi_longitudes.append(lon)
            roi_xs.append(x)
            roi_ys.append(y)

print(len(roi_latitudes), 'candidate neighborhood centers generated.')

2261 candidate neighborhood centers generated.


OK. Now let's calculate two most important things for each location candidate: **number of restaurants in vicinity** (we'll use radius of **250 meters**) and **distance to closest vegan restaurant**.

In [127]:
def count_restaurants_nearby(x, y, restaurants, radius=250):    
    count = 0
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=radius:
            count += 1
    return count

def find_nearest_restaurant(x, y, restaurants):
    d_min = 100000
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=d_min:
            d_min = d
    return d_min

roi_restaurant_counts = []
roi_vegan_distances = []

print('Generating data on location candidates... ', end='')
for x, y in zip(roi_xs, roi_ys):
    count = count_restaurants_nearby(x, y, restaurants, radius=250)
    roi_restaurant_counts.append(count)
    distance = find_nearest_restaurant(x, y, vegan_restaurants)
    roi_vegan_distances.append(distance)
print('done.')

Generating data on location candidates... done.


In [128]:
# Let's put this into dataframe
df_roi_locations = pd.DataFrame({'Latitude':roi_latitudes,
                                 'Longitude':roi_longitudes,
                                 'X':roi_xs,
                                 'Y':roi_ys,
                                 'Restaurants nearby':roi_restaurant_counts,
                                 'Distance to vegan restaurant':roi_vegan_distances})

df_roi_locations.head(10)

Latitude  Longitude             X             Y  Restaurants nearby  \
0 -23.575974 -46.657577 -6.629914e+06 -4.735199e+06                   4   
1 -23.576294 -46.657114 -6.629814e+06 -4.735199e+06                   5   
2 -23.573847 -46.659822 -6.630464e+06 -4.735112e+06                   4   
3 -23.574166 -46.659359 -6.630364e+06 -4.735112e+06                   6   
4 -23.574486 -46.658897 -6.630264e+06 -4.735112e+06                   5   
5 -23.574806 -46.658434 -6.630164e+06 -4.735112e+06                   5   
6 -23.575125 -46.657971 -6.630064e+06 -4.735112e+06                   8   
7 -23.575445 -46.657508 -6.629964e+06 -4.735112e+06                   7   
8 -23.575765 -46.657045 -6.629864e+06 -4.735112e+06                   5   
9 -23.576084 -46.656583 -6.629764e+06 -4.735112e+06                   5   

   Distance to vegan restaurant  
0                    914.802034  
1                    988.233702  
2                    567.060565  
3                    592.706313  
4                    633.280240  
5                    686.139163  
6                    748.685542  
7                    818.702101  
8                    894.436258  
9                    974.555954

OK. Let us now **filter** those locations: we're interested only in **locations with no more than two restaurants in radius of 250 meters**, and **no vegan restaurants in radius of 400 meters**.

In [129]:
good_res_count = np.array((df_roi_locations['Restaurants nearby']<=2))
print('Locations with no more than two restaurants nearby:', good_res_count.sum())

good_ita_distance = np.array(df_roi_locations['Distance to vegan restaurant']>=400)
print('Locations with no vegan restaurants within 400m:', good_ita_distance.sum())

good_locations = np.logical_and(good_res_count, good_ita_distance)
print('Locations with both conditions met:', good_locations.sum())

df_good_locations = df_roi_locations[good_locations]

Locations with no more than two restaurants nearby: 848
Locations with no vegan restaurants within 400m: 1709
Locations with both conditions met: 769


Let's see how this looks on a map.

In [130]:
good_latitudes = df_good_locations['Latitude'].values
good_longitudes = df_good_locations['Longitude'].values

good_locations = [[lat, lon] for lat, lon in zip(good_latitudes, good_longitudes)]

map_bixiga = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_bixiga)
HeatMap(restaurant_latlons).add_to(map_bixiga)
folium.Circle(roi_center, radius=3000, color='white', fill=True, fill_opacity=0.6).add_to(map_bixiga)
folium.Marker(bixiga).add_to(map_bixiga)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_bixiga) 
#folium.GeoJson(berlin_boroughs, style_function=boroughs_style, name='geojson').add_to(map_berlin)
map_bixiga

Looking good. We now have a bunch of locations fairly close to Bixiga, and we know that each of those locations has no more than two restaurants in radius of 250m, and no vegan restaurant closer than 400m. Any of those locations is a potential candidate for a new vegan restaurant, at least based on nearby competition.

Let's now show those good locations in a form of heatmap:

In [131]:
map_bixiga = folium.Map(location=roi_center, zoom_start=14)
HeatMap(good_locations, radius=25).add_to(map_bixiga)
folium.Marker(bixiga).add_to(map_bixiga)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_bixiga)
#folium.GeoJson(berlin_boroughs, style_function=boroughs_style, name='geojson').add_to(map_berlin)
map_bixiga

Looking good. What we have now is a clear indication of zones with low number of restaurants in vicinity, and *no* vegan restaurants at all nearby.

Let us now **cluster** those locations to create **centers of zones containing good locations**. Those zones, their centers and addresses will be the final result of our analysis. 

In [132]:
from sklearn.cluster import KMeans

number_of_clusters = 15

good_xys = df_good_locations[['X', 'Y']].values
kmeans = KMeans(n_clusters=number_of_clusters, random_state=0).fit(good_xys)

cluster_centers = [xy_to_lonlat(cc[0], cc[1]) for cc in kmeans.cluster_centers_]

map_bixiga = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_bixiga)
HeatMap(restaurant_latlons).add_to(map_bixiga)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_bixiga)
folium.Marker(bixiga).add_to(map_bixiga)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=True, fill_opacity=0.25).add_to(map_bixiga)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_bixiga)
#folium.GeoJson(berlin_boroughs, style_function=boroughs_style, name='geojson').add_to(map_berlin)
map_bixiga

Not bad - our clusters represent groupings of most of the candidate locations and cluster centers are placed nicely in the middle of the zones 'rich' with location candidates.

Addresses of those cluster centers will be a good starting point for exploring the neighborhoods to find the best possible location based on neighborhood specifics.

Let's see those zones on a city map without heatmap, using shaded areas to indicate our clusters:

In [81]:
map_bixiga = folium.Map(location=roi_center, zoom_start=14)
folium.Marker(bixiga).add_to(map_bixiga)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#00000000', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_bixiga)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_bixiga)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_bixiga) 
#folium.GeoJson(berlin_boroughs, style_function=boroughs_style, name='geojson').add_to(map_bixiga)
map_bixiga

Let's zoom in on candidate areas in **Kreuzberg**:

In [136]:
map_bixiga = folium.Map(location=[-23.556831106, -46.653830718], zoom_start=15)
folium.Marker(bixiga).add_to(map_bixiga)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_bixiga) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_bixiga)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_bixiga)
map_bixiga

Finaly, let's **reverse geocode those candidate area centers to get the addresses** which can be presented to stakeholders.

In [133]:
candidate_area_addresses = []
print('==============================================================')
print('Addresses of centers of areas recommended for further analysis')
print('==============================================================\n')
for lon, lat in cluster_centers:
    addr = get_address(google_api_key, lat, lon).replace(', Brazil', '')
    candidate_area_addresses.append(addr)    
    x, y = lonlat_to_xy(lon, lat)
    d = calc_xy_distance(x, y, bixiga_x, bixiga_y)
    print('{}{} => {:.1f}km from Bixiga'.format(addr, ' '*(50-len(addr)), d/1000))

Addresses of centers of areas recommended for further analysis

Praça Quatorze Bis, 82 - Bela Vista, São Paulo - SP, 01312-010 => 0.9km from Bixiga
R. Afonso de Freitas, 615 - Paraíso, São Paulo - SP, 04006-052 => 3.6km from Bixiga
R. Martiniano de Carvalho, 612 - Bela Vista, São Paulo - SP => 1.4km from Bixiga
Alameda Franca, 629 - Jardim Paulista, São Paulo - SP, 01423-070 => 2.9km from Bixiga
R. Itapeva, 500 - Bela Vista, São Paulo - SP, 01332-010 => 1.5km from Bixiga
R. Urano, 1 - Aclimação, São Paulo - SP, 01532-000 => 2.9km from Bixiga
Alameda Sarutaiá, 185 - Jardim Paulista, São Paulo - SP, 01403-010 => 2.7km from Bixiga
R. Maria José, 12 - Bela Vista, São Paulo - SP, 01324-010 => 0.5km from Bixiga
Vergueiro Metro Station - Rua Vergueiro, 790 - Liberdade, São Paulo - SP, 01504-001 => 2.3km from Bixiga
R. dos Bombeiros - Paraíso, São Paulo - SP         => 3.7km from Bixiga
Rua Conde de São Joaquim, 359 - Bela Vista, São Paulo - SP, 01320-010 => 1.1km from Bixiga
R. dos Franceses,

This concludes our analysis. We have created 15 addresses representing centers of zones containing locations with low number of restaurants and no vegan restaurants nearby, all zones being fairly close to the Bixiga area (all less than 4km from Bixiga, and about half of those less than 2km from it). Although zones are shown on map with a radius of ~500 meters (green circles), their shape is actually very irregular and their centers/addresses should be considered only as a starting point for exploring area neighborhoods in search for potential restaurant locations. Most of the zones are located around the Paulista Avenue, which we have identified as interesting due to being popular with tourists, fairly close to Bixiga and well connected by public transport.

In [134]:
map_bixiga = folium.Map(location=roi_center, zoom_start=14)
folium.Circle(bixiga, radius=50, color='red', fill=True, fill_color='red', fill_opacity=1).add_to(map_bixiga)
for lonlat, addr in zip(cluster_centers, candidate_area_addresses):
    folium.Marker([lonlat[1], lonlat[0]], popup=addr).add_to(map_bixiga) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.05).add_to(map_bixiga)
map_bixiga

## Results and Discussion <a name="results"></a>

Our analysis shows that although there is a great number of restaurants around Bixiga, there are pockets of low restaurant density fairly close to this area. Highest concentration of restaurants was detected northeast and southwest from Bixiga, so we focused our attention to areas south, south-east and east, corresponding to area around the Paulista Avenue.

After directing our attention to this more narrow area of interest, we first created a dense grid of location candidates (spaced 100m appart); those locations were then filtered so that those with more than two restaurants in radius of 250m and those with a vegan restaurant closer than 400m were removed.

Those location candidates were then clustered to create zones of interest which contain greatest number of location candidates. Addresses of centers of those zones were also generated using reverse geocoding to be used as markers/starting points for more detailed local analysis based on other factors.

Result of all this is 15 zones containing largest number of potential new restaurant locations based on number of and distance to existing venues - both restaurants in general and vegan restaurants particularly. This, of course, does not imply that those zones are actually optimal locations for a new restaurant! Purpose of this analysis was to only provide info on areas close to Bixiga but not crowded with existing restaurants (particularly vegan) - it is entirely possible that there is a very good reason for small number of restaurants in any of those areas, reasons which would make them unsuitable for a new restaurant regardless of lack of competition in the area. Recommended zones should therefore be considered only as a starting point for more detailed analysis which could eventually result in location which has not only no nearby competition but also other factors taken into account and all other relevant conditions met.

## Conclusion <a name="conclusion"></a>

Purpose of this project was to identify Sao Paulo areas close to Bixiga neighborhood with low number of restaurants (particularly vegan restaurants) in order to aid stakeholders in narrowing down the search for optimal location for a new vegan restaurant. By calculating restaurant density distribution from Foursquare data we have first identified general boroughs that justify further analysis (Paulista Avenue), and then generated extensive collection of locations which satisfy some basic requirements regarding existing nearby restaurants. Clustering of those locations was then performed in order to create major zones of interest (containing greatest number of potential locations) and addresses of those zone centers were created to be used as starting points for final exploration by stakeholders.

Final decission on optimal restaurant location will be made by stakeholders based on specific characteristics of neighborhoods and locations in every recommended zone, taking into consideration additional factors like attractiveness of each location (proximity to park or water), levels of noise / proximity to major roads, real estate availability, prices, social and economic dynamics of every neighborhood etc.